In [ ]:
# Runtime > Change runtime type > Hardware accelerator: GPU
# Install Driver
!nvidia-smi

Fri Mar 10 06:08:27 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.85.12    Driver Version: 525.85.12    CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   67C    P0    29W /  70W |   2275MiB / 15360MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
# Install LLM tools
! pip install -q langchain gpt-index llama-index transformers sentence_transformers

  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 87.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.2/199.2 KB 22.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 16.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.1/49.1 KB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.5/73.5 KB 8.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.8/62.8 KB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 65.7 MB/s eta 0:00:00


In [ ]:
# Install visualization tools
!pip install -q gradio

In [ ]:
# Import Libraries
import gradio as gr

## Features
from llama_index import Document

## Model
from langchain.llms.base import LLM
from llama_index import LLMPredictor, GPTSimpleVectorIndex
from transformers import pipeline
import torch

from langchain.embeddings.huggingface import HuggingFaceEmbeddings
from llama_index import LangchainEmbedding

In [ ]:
# Feature Functions

## Text to Document
def text_to_document(input_text):
    text_list = [input_text]
    return [Document(t) for t in text_list]  # documents

In [ ]:
# Model Functions & Class
class FlanLLM(LLM):
    model_name = "google/flan-t5-base"
    pipeline = pipeline("text2text-generation", model=model_name,
                        device=0, model_kwargs={"torch_dtype": torch.bfloat16})

    def _call(self, prompt, stop=None):
        return self.pipeline(prompt, max_length=9999)[0]["generated_text"]

    def _identifying_params(self):
        return {"name_of_model": self.model_name}

    def _llm_type(self):
        return "custom"

llm_predictor = LLMPredictor(llm=FlanLLM())
hfemb = HuggingFaceEmbeddings()
embed_model = LangchainEmbedding(hfemb)

def document_to_index(documents):
    global index
    index = GPTSimpleVectorIndex(
        documents, embed_model=embed_model, llm_predictor=llm_predictor)
    return('Index successfully saved.')

def query_and_response(chat_history, user_query):
    bot_response = index.query(user_query)
    response = ""
    for letter in ''.join(bot_response.response):
        response += f'{letter}'
        yield chat_history + [(user_query, response)]

In [ ]:
# App
def text_to_index(input_text):
    documents = text_to_document(input_text)
    document_to_index(documents)

with gr.Blocks() as demo:
    gr.Markdown('Q&A Chatbot')
    with gr.Tab("Input Text"):
        text_input = gr.Textbox()
        text_output = gr.Textbox()
        text_button = gr.Button("Learn From Text")
        text_button.click(text_to_index, text_input, text_output)
    with gr.Tab("Chat"):
        chatbot = gr.Chatbot()
        message = gr.Textbox("Please summarize this document")
        message.submit(query_and_response, [chatbot, message], chatbot)


Setting queue=True in a Colab notebook requires sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
Running on public URL: https://1010e1d1a156b247ae.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades (NEW!), check out Spaces: https://huggingface.co/spaces


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://1010e1d1a156b247ae.gradio.live
